In [1]:
import logging
import tensorflow as tf
import mlflow
import random
import pandas as pd
import numpy as np

import sys
import os

module_path = os.path.abspath(os.path.join('..'))
if module_path not in sys.path:
    sys.path.append(module_path)

sys.argv.clear()
sys.argv.append("")

In [2]:
from src import config
from src.features import preprocessing,sequences,knowledge
from src.training import models
from src import refinement

# four types of knowledge for Huawei:
# gram, text, causal, log template(gram_logs)
experiment_config = config.ExperimentConfig()
experiment_config.model_type = "gram"
experiment_config.sequence_type = "huawei_logs"

model_config = models.config.ModelConfig()
model_config.rnn_type: str = "gru"

# keep all other default configurations 
huawei_preprocessor_config = preprocessing.huawei.HuaweiPreprocessorConfig()
# for template_hierarchy
huawei_preprocessor_config.use_log_hierarchy = True

sequence_config = sequences.config.SequenceConfig()
knowledge_config = knowledge.config.KnowledgeConfig()
refinement_config = refinement.config.RefinementConfig()

In [3]:
def log_all_configs_to_mlflow():
    for config in [
        experiment_config,
        huawei_preprocessor_config,
        sequence_config,
        model_config,
        knowledge_config,
        refinement_config,
    ]:
        for config_name, config_value in vars(config).items():
            full_config_name = config.__class__.__name__ + config_name
            mlflow.log_param(full_config_name, str(config_value))

In [4]:
mlflow.set_experiment("Domain Guided Monitoring")
with mlflow.start_run() as run:
    run_id = run.info.run_id
logging.info("Starting run %s", run_id)
tf.random.set_seed(experiment_config.tensorflow_seed)
random.seed(experiment_config.random_seed)

## Load Huawei sequences

In [5]:
sequence_preprocessor = preprocessing.ConcurrentAggregatedLogsPreprocessor(
    huawei_preprocessor_config,
)
sequence_column_name = sequence_preprocessor.sequence_column_name
sequence_df = sequence_preprocessor.load_data()

transformer = sequences.transformer.NextPartialSequenceTransformerFromDataframe(sequence_config)
metadata = transformer.collect_metadata(sequence_df, sequence_column_name)

/tmp/ipykernel_52464/3819484698.py:5: DtypeWarning: Columns (23,24,25,28) have mixed types.Specify dtype option on import or set low_memory=False.
  sequence_df = sequence_preprocessor.load_data()
Generating DRAIN clusters from log_df: 100%|████████████████████| 970/970 [00:00<00:00, 14243.76it/s]


## Generate dataset

In [6]:
sequence_df_pkl_file: str = "data/sequences_df.pkl"
sequence_df.to_pickle(sequence_df_pkl_file)

train_sequences, test_sequences = transformer._split_train_test(sequence_df, sequence_column_name)

def generate(for_train):
    relevant_sequences = train_sequences if for_train else test_sequences
    for sequence in relevant_sequences:
        split_sequences = transformer._split_sequence(sequence)
        for split_sequence in split_sequences:
            transformer._translate_and_pad(split_sequence, metadata)
            yield split_sequence.x_vecs_stacked, split_sequence.y_vec

def generate_train():
    return generate(for_train=True)

def generate_test():
    return generate(for_train=False)

In [7]:
train_dataset = (
    tf.data.Dataset.from_generator(
        generate_train,
        output_types=(tf.float32, tf.float32),
    )
    .shuffle(
        experiment_config.dataset_shuffle_buffer,
        seed=experiment_config.dataset_shuffle_seed,
        reshuffle_each_iteration=True,
    )
    .batch(experiment_config.batch_size)
    .prefetch(tf.data.experimental.AUTOTUNE)
)

test_dataset = (
    tf.data.Dataset.from_generator(
        generate_test,
        output_types=(tf.float32, tf.float32),
    )
    .batch(experiment_config.batch_size)
    .prefetch(tf.data.experimental.AUTOTUNE)
)

2022-05-30 07:58:18.716013: W tensorflow/stream_executor/platform/default/dso_loader.cc:55] Could not load dynamic library 'libcuda.so.1'; dlerror: libcuda.so.1: cannot open shared object file: No such file or directory
2022-05-30 07:58:18.716031: E tensorflow/stream_executor/cuda/cuda_driver.cc:313] failed call to cuInit: UNKNOWN ERROR (303)
2022-05-30 07:58:18.716043: I tensorflow/stream_executor/cuda/cuda_diagnostics.cc:156] kernel driver does not appear to be running on this host (hj-ubuntu): /proc/driver/nvidia/version does not exist
2022-05-30 07:58:18.716527: I tensorflow/core/platform/cpu_feature_guard.cc:143] Your CPU supports instructions that this TensorFlow binary was not compiled to use: AVX2 FMA
2022-05-30 07:58:18.740051: I tensorflow/core/platform/profile_utils/cpu_utils.cc:102] CPU Frequency: 2599990000 Hz
2022-05-30 07:58:18.740712: I tensorflow/compiler/xla/service/service.cc:168] XLA service 0x7fe178000b60 initialized for platform Host (this does not guarantee that 

## Generate log template

In [8]:
hierarchy_preprocessor = preprocessing.ConcurrentAggregatedLogsHierarchyPreprocessor(
    config = huawei_preprocessor_config
)

pd.set_option('display.max_columns', None) 
pd.set_option('display.max_rows', None) 
pd.set_option('max_colwidth',100)

### Step 1 Load log-only data 

In [14]:
huawei_df = sequence_preprocessor._load_log_only_data()

/home/jin/miniconda3/envs/healthcare-aiops/lib/python3.8/site-packages/IPython/core/interactiveshell.py:3444: DtypeWarning: Columns (23,24,25,28) have mixed types.Specify dtype option on import or set low_memory=False.
  exec(code_obj, self.user_global_ns, self.user_ns)
Generating DRAIN clusters from log_df: 100%|████████████████████| 970/970 [00:00<00:00, 14264.19it/s]


In [15]:
huawei_df.head(100)

Hostname log_level                    programname  \
0   wally113      INFO      neutron-openvswitch-agent   
1   wally113      INFO      neutron-openvswitch-agent   
2   wally113   WARNING                       keystone   
3   wally113      INFO                     glance-api   
4   wally113      INFO                       nova-api   
5   wally113     ERROR                       nova-api   
6   wally113      INFO                       nova-api   
7   wally113      INFO                       nova-api   
8   wally113      INFO                 neutron-server   
9   wally113      INFO                       nova-api   
10  wally113      INFO                     glance-api   
11  wally113      INFO                     glance-api   
12  wally113      INFO                       nova-api   
13  wally113      INFO                 neutron-server   
14  wally113            keystone-apache-public-access   
15  wally113            keystone-apache-public-access   
16  wally113            keystone-apache-public-access   
17  wally113            keystone-apache-public-access   
18  wally113            keystone-apache-public-access   
19  wally113            keystone-apache-public-access   
20  wally113            keystone-apache-public-access   
21  wally113            keystone-apache-public-access   
22  wally113            keystone-apache-public-access   
23  wally113            keystone-apache-public-access   
24  wally113            keystone-apache-public-access   
25  wally113            keystone-apache-public-access   
26  wally113            keystone-apache-public-access   
27  wally113            keystone-apache-public-access   
28  wally113            keystone-apache-public-access   
29  wally113            keystone-apache-public-access   
30  wally113            keystone-apache-public-access   
31  wally113            keystone-apache-public-access   
32  wally113            keystone-apache-public-access   
33  wally113            keystone-apache-public-access   
34  wally113            keystone-apache-public-access   
35  wally113            keystone-apache-public-access   
36  wally113            keystone-apache-public-access   
37  wally113            keystone-apache-public-access   
38  wally113            keystone-apache-public-access   
39  wally113            keystone-apache-public-access   
40  wally113             keystone-apache-admin-access   
41  wally113            keystone-apache-public-access   
42  wally113            keystone-apache-public-access   
43  wally113             keystone-apache-admin-access   
44  wally113            keystone-apache-public-access   
45  wally113            keystone-apache-public-access   
46  wally113            keystone-apache-public-access   
47  wally113            keystone-apache-public-access   
48  wally113             keystone-apache-admin-access   
49  wally113            keystone-apache-public-access   
50  wally113            keystone-apache-public-access   
51  wally113            keystone-apache-public-access   
52  wally113            keystone-apache-public-access   
53  wally113            keystone-apache-public-access   
54  wally113      INFO                       nova-api   
55  wally113   WARNING                       nova-api   
56  wally113      INFO                       nova-api   
57  wally113      INFO                       nova-api   
58  wally113      INFO                       nova-api   
59  wally113   WARNING                       nova-api   
60  wally113      INFO      neutron-openvswitch-agent   
61  wally113      INFO      neutron-openvswitch-agent   
62  wally113      INFO      neutron-openvswitch-agent   
63  wally113      INFO      neutron-openvswitch-agent   
64  wally113      INFO      neutron-openvswitch-agent   
65  wally113            keystone-apache-public-access   
66  wally113            keystone-apache-public-access   
67  wally113            keystone-apache-public-access   
68  wally113            keystone-apache-public-access   
69  wally113  

### Sep 2 Load log-only hierarchy (different from attribute-only hierarchy)

In [16]:
relevant_log_columns = set(
    [x for x in sequence_preprocessor.relevant_columns if "log_cluster_template" in x]
    + ["coarse_log_cluster_path"]
)

In [17]:
attribute_hierarchy = hierarchy_preprocessor._load_attribute_hierarchy(
    huawei_df, set(["coarse_log_cluster_path"])
)

Loading hierarchy for column coarse_log_cluster_path: 100%|███████| 469/469 [00:04<00:00, 113.62it/s]


In [18]:
attribute_hierarchy

parent_id  \
0                                                                                                root   
1                                                                             coarse_log_cluster_path   
2                                                                         coarse_log_cluster_path->38   
3                                                                      coarse_log_cluster_path->38->*   
4                                                                 coarse_log_cluster_path->38->*->nov   
5                                                              coarse_log_cluster_path->38->*->nov->*   
6                                                                             coarse_log_cluster_path   
7                                                                         coarse_log_cluster_path->18   
8                                                                coarse_log_cluster_path->18->running   
9                                                     coarse_log_cluster_path->18->running->novaosapi   
10                                           coarse_log_cluster_path->18->running->novaosapi->compute   
11                                                                            coarse_log_cluster_path   
12                                                                        coarse_log_cluster_path->28   
13                                                                   coarse_log_cluster_path->28->sql   
14                                                       coarse_log_cluster_path->28->sql->connection   
15                                               coarse_log_cluster_path->28->sql->connection->failed   
16                                                                            coarse_log_cluster_path   
17                                                                         coarse_log_cluster_path->4   
18                                                                coarse_log_cluster_path->4->loading   
19                                                          coarse_log_cluster_path->4->loading->core   
20                                                  coarse_log_cluster_path->4->loading->core->plugin   
21                                                                            coarse_log_cluster_path   
22                                                                       coarse_log_cluster_path->107   
23                                                             coarse_log_cluster_path->107->instance   
24                                                          coarse_log_cluster_path->107->instance->*   
25                                                   coarse_log_cluster_path->107->instance->*->error   
26                                                                            coarse_log_cluster_path   
27                                                                        coarse_log_cluster_path->25   
28                                                                     coarse_log_cluster_path->25->*   
29                                                                coarse_log_cluster_path->25->*->nov   
30                                                             coarse_log_cluster_path->25->*->nov->*   
31                                                                            coarse_log_cluster_path   
32                                                                         coarse_log_cluster_path->5   
33                                                                   coarse_log_cluster_path->5->rbac   
34                                                           coarse_log_cluster_path->5->rbac->policy   
35                                                       coarse_log_cluster_path->5->rbac->policy->is   
36                                                                            coarse_log_cluster_path   
37                                                                         coarse_log_cluster_path->4 

In [21]:
attribute_hierarchy.append(
    hierarchy_preprocessor._load_log_hierarchy(huawei_df, relevant_log_columns),
    ignore_index=True,
).drop_duplicates().reset_index(drop=True)

Adding huawei log hierarchy: 100%|████████████████████████| 169230/169230 [00:13<00:00, 12430.85it/s]


parent_id  \
0                                                                                                    root   
1                                                                                 coarse_log_cluster_path   
2                                                                             coarse_log_cluster_path->38   
3                                                                          coarse_log_cluster_path->38->*   
4                                                                     coarse_log_cluster_path->38->*->nov   
5                                                                  coarse_log_cluster_path->38->*->nov->*   
6                                                                                 coarse_log_cluster_path   
7                                                                             coarse_log_cluster_path->18   
8                                                                    coarse_log_cluster_path->18->running   
9                                                         coarse_log_cluster_path->18->running->novaosapi   
10                                               coarse_log_cluster_path->18->running->novaosapi->compute   
11                                                                                coarse_log_cluster_path   
12                                                                            coarse_log_cluster_path->28   
13                                                                       coarse_log_cluster_path->28->sql   
14                                                           coarse_log_cluster_path->28->sql->connection   
15                                                   coarse_log_cluster_path->28->sql->connection->failed   
16                                                                                coarse_log_cluster_path   
17                                                                             coarse_log_cluster_path->4   
18                                                                    coarse_log_cluster_path->4->loading   
19                                                              coarse_log_cluster_path->4->loading->core   
20                                                      coarse_log_cluster_path->4->loading->core->plugin   
21                                                                                coarse_log_cluster_path   
22                                                                           coarse_log_cluster_path->107   
23                                                                 coarse_log_cluster_path->107->instance   
24                                                              coarse_log_cluster_path->107->instance->*   
25                                                       coarse_log_cluster_path->107->instance->*->error   
26                                                                                coarse_log_cluster_path   
27                                                                            coarse_log_cluster_path->25   
28                                                                         coarse_log_cluster_path->25->*   
29                                                                    coarse_log_cluster_path->25->*->nov   
30                                                                 coarse_log_cluster_path->25->*->nov->*   
31                                                                                coarse_log_cluster_path   
32                                                                             coarse_log_cluster_path->5   
33                                                                       coarse_log_cluster_path->5->rbac   
34                                                               coarse_log_cluster_path->5->rbac->policy   
35                                                           coarse_log_cluster_path->5->rbac->policy->is   
36                                                             

In [22]:
attribute_hierarchy

parent_id  \
0                                                                                                root   
1                                                                             coarse_log_cluster_path   
2                                                                         coarse_log_cluster_path->38   
3                                                                      coarse_log_cluster_path->38->*   
4                                                                 coarse_log_cluster_path->38->*->nov   
5                                                              coarse_log_cluster_path->38->*->nov->*   
6                                                                             coarse_log_cluster_path   
7                                                                         coarse_log_cluster_path->18   
8                                                                coarse_log_cluster_path->18->running   
9                                                     coarse_log_cluster_path->18->running->novaosapi   
10                                           coarse_log_cluster_path->18->running->novaosapi->compute   
11                                                                            coarse_log_cluster_path   
12                                                                        coarse_log_cluster_path->28   
13                                                                   coarse_log_cluster_path->28->sql   
14                                                       coarse_log_cluster_path->28->sql->connection   
15                                               coarse_log_cluster_path->28->sql->connection->failed   
16                                                                            coarse_log_cluster_path   
17                                                                         coarse_log_cluster_path->4   
18                                                                coarse_log_cluster_path->4->loading   
19                                                          coarse_log_cluster_path->4->loading->core   
20                                                  coarse_log_cluster_path->4->loading->core->plugin   
21                                                                            coarse_log_cluster_path   
22                                                                       coarse_log_cluster_path->107   
23                                                             coarse_log_cluster_path->107->instance   
24                                                          coarse_log_cluster_path->107->instance->*   
25                                                   coarse_log_cluster_path->107->instance->*->error   
26                                                                            coarse_log_cluster_path   
27                                                                        coarse_log_cluster_path->25   
28                                                                     coarse_log_cluster_path->25->*   
29                                                                coarse_log_cluster_path->25->*->nov   
30                                                             coarse_log_cluster_path->25->*->nov->*   
31                                                                            coarse_log_cluster_path   
32                                                                         coarse_log_cluster_path->5   
33                                                                   coarse_log_cluster_path->5->rbac   
34                                                           coarse_log_cluster_path->5->rbac->policy   
35                                                       coarse_log_cluster_path->5->rbac->policy->is   
36                                                                            coarse_log_cluster_path   
37                                                                         coarse_log_cluster_path->4 

### Step 3 Build hierarchy from daraframe

In [23]:
hierarchy = knowledge.HierarchyKnowledge(
    config=knowledge_config,
)
hierarchy.build_hierarchy_from_df(attribute_hierarchy, metadata.x_vocab)

Building Hierarchy from df: 2340it [00:00, 17133.68it/s]


## Genarate model

In [ ]:
# load model
model = models.GramModel()

# build model
model.build(metadata, hierarchy)

## Run Experiment

In [ ]:
# train model
model.train_dataset(
    train_dataset,
    test_dataset,
    experiment_config.multilabel_classification,
    experiment_config.n_epochs,
)

In [ ]:
# logging dataset info
mlflow.log_metric("train_size", len([x for x in train_dataset]))
mlflow.log_metric("test_size", len([x for x in test_dataset]))
mlflow.log_metric("x_vocab_size", len(metadata.x_vocab))
mlflow.log_metric("y_vocab_size", len(metadata.y_vocab))

# generate artifacts
# skip

# set mlflow tags
mlflow.set_tag("sequence_type", experiment_config.sequence_type)
mlflow.set_tag("model_type", experiment_config.model_type)
if len(metadata.y_vocab) == 1:
    mlflow.set_tag("task_type", "risk_prediction")
else:
    mlflow.set_tag("task_type", "sequence_prediction")

logging.info("Finished run %s", run_id)